In [54]:
import geopandas as gpd
import folium
import math


# data
gdf = gpd.read_file("prt-stops.geojson")

# center, map
center = [gdf.geometry.y.mean(), gdf.geometry.x.mean()]
m = folium.Map(location=center, zoom_start=12)


# bus stop
for _, row in gdf.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=1,
        color='red',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)

m.add_child(folium.LatLngPopup())

m.save("pittsburgh_bus_stops.html")
m


In [50]:
def count_stops_simple(lat, lon, radius_miles, gdf):
    """
    lat, lon : center coordinates (degrees)
    radius_miles : radius (miles)
    gdf : preloaded GeoDataFrame (assumed EPSG:4326)
    """
    # Approximation: 1 degree of latitude ≈ 69 miles, longitude ≈ 69 * cos(latitude)
    lat_per_mile = 1 / 69.0
    lon_per_mile = 1 / (69.0 * math.cos(math.radians(lat)))

    # Convert radius to degrees
    dlat = radius_miles * lat_per_mile
    dlon = radius_miles * lon_per_mile

    count = 0
    for point in gdf.geometry:
        plat, plon = point.y, point.x
        # Quick bounding-box check
        if abs(plat - lat) <= dlat and abs(plon - lon) <= dlon:
            # Compute simple Euclidean distance in miles
            dist = math.sqrt(((plat - lat)/lat_per_mile)**2 + ((plon - lon)/lon_per_mile)**2)
            if dist <= radius_miles:
                count += 1
    return count

num = count_stops_simple(40.4406, -79.9959, 0.1, gdf)
print(num)

9


In [52]:
keys_file = "Neighborhood.txt"
values_file = "Latitude.txt"
latitude = {}


with open(keys_file, "r", encoding="utf-8") as kf, open(values_file, "r", encoding="utf-8") as vf:
    for key_line, value_line in zip(kf, vf):
        key = key_line.strip()
        value = value_line.strip()
        if value == '':
            continue
        latitude[key] = float(value)
#print(latitude)

values_file = "longitude.txt"
longitude = {}
with open(keys_file, "r", encoding="utf-8") as kf, open(values_file, "r", encoding="utf-8") as vf:
    for key_line, value_line in zip(kf, vf):
        key = key_line.strip()
        value = value_line.strip()
        if value == '':
            continue
        longitude[key] = float(value)
#print(longitude)

result = {}
for key in latitude:
    if key == '':
        continue
    num = count_stops_simple(float(latitude[key]),float(longitude[key]), 0.5, gdf)
    result[key] = num

#print(result)

sorted_data = dict(sorted(result.items(), key=lambda x: x[1]))
print(sorted_data)


{'New Homestead': 0, 'Swisshelm Park': 4, 'Banksville': 6, 'Esplen': 11, 'Brookline': 12, 'Ridgemont': 12, 'Hays': 12, 'Oakwood': 13, 'Squirrel Hill South': 14, 'Lincoln Place': 17, 'Fairywood': 18, 'Carrick': 19, 'Sheraden': 21, 'Overbrook': 21, 'Perry North': 23, 'Arlington Heights': 23, 'East Carnegie': 24, 'Westwood': 25, 'Duquesne Heights': 25, 'West End': 28, 'Greenfield': 29, 'Windgap': 29, 'Elliott': 29, 'South Oakland': 30, 'St. Clair': 30, 'Central Lawrenceville': 32, 'Stanton Heights': 32, 'Chateau': 32, 'Arlington': 33, 'Bon Air': 36, 'Summer Hill': 36, 'Marshall-Shadeland': 37, 'Regent Square': 38, 'Glen Hazel': 38, 'Crafton Heights': 39, 'Brighton Heights': 39, 'East Hills': 40, 'Chartiers City': 40, 'Spring Hill-City View': 41, 'North Shore': 43, 'Troy Hill': 43, 'South Side Flats': 44, 'Upper Lawrenceville': 44, 'Spring Garden': 44, 'Knoxville': 47, 'Beechview': 48, 'Mt. Oliver': 49, 'Larimer': 51, 'Hazelwood': 53, 'Morningside': 53, 'Northview Heights': 54, 'Middle Hil

In [53]:
for key in latitude:
    folium.CircleMarker(
        location=[float(latitude[key]), float(longitude[key])],
        radius=1,
        color='blue',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)
    draw_circle_map(latitude[key],longitude[key],0.3,m)

m.add_child(folium.LatLngPopup())

m.save("pittsburgh_bus_stops.html")
m